# <img src="http://pyntacle.css-mendel.it/images/logo_simpler-u708-fr3.png" align="left"/> <br> Case Study 1:  The search for key players in ecological food webs


<br>

*Pyntacle version: 1.3.2*

---

# Table of Contents

- [Introduction](#intro)
- [Data description](#data)
- [Assessing the importance of species using single-node-resolution centrality](#met)
- [Key player search (kp-search) in food webs: *reachability* (m-reach)](#kppos)
- [Key player search (kp-search) in food webs: *fragmentation* (F)](#kpneg)
- [Evaluation of a random model](#rand) 
- [Conclusions](#end)

---

## Introduction <a id="intro"></a> 
---
This case study will show how to determine *key players* and group effects in food webs. It will not describe the theory behind the key-player metrics developed in Pyntacle. The interested reader may in fact refer to [What Are Key-players](http://pyntacle.css-mendel.it/resources/kp_guide/kp_guide.html) section for detailed explanation of the key-player metrics, to the [Quick Start Guide](http://pyntacle.css-mendel.it/resources/tutorials/startup_guide/Quick%20Start%20Guide.html) for getting acquainted with the basic Pyntacle commands, and to the [Pyntacle Library](http://pyntacle.css-mendel.it/resources/command_line_manual/command_line_manual.html). 

Food webs represent trophic relationships among species and are increasingly used to integrate ecological data and to determine ecosystem properties. Some species, like earthworms, beavers or the krill, have large effects on others. These play an extraordinarily important role in the ecosystem where they live and occupy crucial positions within the inter-specific interaction networks (for example, in the food webs). For this, they are called keystone species ([Jordan, 2009](https://www.ncbi.nlm.nih.gov/pmc/articles/PMC2685432/pdf/rstb20080335.pdf)). Identifying keystone species is also important in conservation management. One way to do that is through network theory ([Harary 1961](http://pyntacle.css-mendel.it/resources/tutorials/cs1/Harary1961.pdf), [Jordán et al. 1999](http://www.jstor.org/stable/3546650?seq=1#page_scan_tab_contents)).

In a network perspective, nodes in a food web are organisms (species or their larger groups). Links among nodes represent feeding relationships. The direction of links is not considered here: although materials flow from resource to consumer, ecological effects (e.g. control) flow in both directions. The weights on links (how much material is transfered) is also not considered here, although typically this information is available and can be used for other kinds of analysis, such as to detect differences in species consumption rates (see ([D’Alello,2016](https://www.nature.com/articles/srep21806)). The sign of links is implicitly clear (positive from resource to consumer and negative from consumer to resource), but also not considered here. Then, this case study will deal with a binary, symmetrical and unsigned graph representing the Mauritania Food web (described in the next section). It will be first analyzed locally, namely the centrality of key species will be assessed by node centrality indices, and later collectively by the Pyntacle’s key player metrics, to capture their eventual group effects. We will then compare the two analysis results, between them and with those obtained with a null model created using `pyntacle generate`, the network generator that recreates *in silico* graphs that follow predefined and well-known topologies. 

In brief, the case study will follow this scheme:
1. Assess the importance of species in the food web using single node centralities obtained through `pyntacle metrics local`;
2. Search for node sets that maximize a key player *rechability* index, m-reach, a proxy for node connectivity, using the `pyntacle keyplayer kp-finder` tool;
3. Find core species whose removal in the food web disrupts network connectivity using a *fragmentation* key player metric, F;
4. Compare the changes in the fragmentation index of the food web against a random (null) model.

This analysis was inspired by our [publication](https://www.hindawi.com/journals/complexity/2018/1979214/) on food web topologies done in collaboration with the Network Ecology team of the Danube Research Institute in Budapest led by Prof. Jordàn.

All the starting data and the corresponding results can be downloaded from [this link](http://pyntacle.css-mendel.it/resources/tutorials/cs1/Pyntacle_CS1.zip).

## Data Description <a id="data"></a> 
---

The *Mauritania food web* is a network describing trophic relationships among marine species in the Exclusive Economic Zone (ZEE) of Mauritania sea territories. It has been firstly described in the [2004 Fisheries Centre research Report](http://pyntacle.css-mendel.it/resources/tutorials/cs1/mauritania_orig_article.pdf) (Chapter 4: *Modèle écotrophique de la ZEE mauritanienne: comparaison de deux périodes (1987 et 1998)*)

It is made by 37 organisms (*N* = 37) and 284 feeding interactions among organisms (*E* = 284). Nodes depict marine species, whose names are described in the following table:

| Species ID | Species Full Name |
| :--- | ---: |
| **Orq** | Killer Whale |
| **Dauph** | Dolphin |
| **Ois** | Sea Birds |
| **SelLPred** | Large selachians - predators |
| **SelLInv** | Large selachians - invertebrates |
| **RaieM** | Small rays |
| **ThonHau** | Deep-sea tuna|
|  **ThonCot** | Coastal tuna |
|  **MesoPred** | Mesopelagics - predators |
|  **MesoInv** | Mesopelagics - invertebrates |
|  **BathySPred** | Bathydemersals - predators|
|  **BathySInv** | Bathydemersals - invertebrates |
|  **Merlu** | Hake |
|  **Spar** | Commercial sparids |
|  **DemLPred** | Large demersals - predators|
|  **DenLInv** | Large demersals - invertebrates |
|  **DemMPred** | Medium demersals - predators |
|  **DemMInv** | Medium demersals - invertebrates |
|  **DemSPred** | Small demersals - predators |
|  **DemSInv** | Small demersals  - invertebrates|
|  **Mugi** | Mugilidae |
|  **Sabre** | Saberfish |
|  **PelLPred** | Large pelagics - predators |
|  **PelDInv** | Large pelagics - invertebrates |
|  **PelMPl** | Small pelagics - planktivores |
|  **Maq** | Mackerel |
|  **Clup** | Clupeids |
|  **Chinch** | Horse Mackerel|
|  **CephaCom** | Commercial cephalopods |
|  **CephaNonCom** | Non-commercial cephalopods |
|  **MacroBenth** | Marcrobenthos |
|  **CrusCom** | Commercial crustaceans|
|  **CrusNonCom** | Non-commercial crustaceans|
|  **MacroZoopl** | Macrozooplankton |
|  **MesoZoopl** | Mesozooplankton |
|  **MicroZoopl** | Microzooplankton |
|  **ProdPrim** | Primary producers |

The network file has already been symmetrized and the trophic weights have been removed to make it compliant to the Pyntacle's [minimum requirements](http://pyntacle.css-mendel.it/requirements.html). 
The network is stored in a text file, which is a binary adjacency matrix with labels. It can be downloaded from [here](https://pyntacle.css-mendel.it/resources/tutorials/cs1/mauritania.adjm). 

For a detailed description of the adjacency matrix file format, have a look at the [file formats](http://pyntacle.css-mendel.it/resources/file_formats/file_formats.html) guide. 

## Assessing the importance of species using single-node centrality <a id="met"></a> 
---

Assessing the importance of nodes in networks is possible by several centrality indices. In Ecology, this problem was faced by [Paine, 1966](https://biology.unm.edu/jhbrown/Documents/511Readings/Paine%201966.pdf) and [Bond, 1993]( https://www.springer.com/gp/book/9783540581031). A set of local topological indices are implemented in Pyntacle and the way to calculate them is as simple as typing:

`pyntacle metrics local -i mauritania.adjm -d ./`

where `-i` specifies the path to the input adjacency matrix and `-d` is the directory that will store results. From here onwards, we assume that Pyntacle is running on the same directory of the input files, and that the results are stored in the same directory. **Note** that in this use case, we are calculating the centrality indices of all nodes. Users can alternatively opt-in to compute these indices for a selected subset of nodes by means of the `--nodes` argument, passing a comma-separated list of the desired nodes. A complete list of all the arguments existing for each Pyntacle commands is available in the [command line guide](http://pyntacle.css-mendel.it/resources/command_line_manual/command_line_manual.html).

Pyntacle will produce a report, in tab-separated format, storing all the computed local metrics. The name of the file will contain a prefix (e.g., *Report_mauritania_Local_*) and a suffix with the analysis execution date and time (e.g., 2018-08-09-175151). Optionally, the user may opt to generate the report in a comma-separated format or as an Excel spreadsheet, by assigning `csv` or the `xlsx` text to the `-r/--report-format` argument. The report will contain a first part continaing general information:

| Network overview | |	
| --- | ---| 
|Graph name |	mauritania|
|Number of Components	 | 1|
|Nodes	| 37|
|Edges	| 284|

This part is common to all Pyntacle reports and gives a quick overview of the feature of the input graph.
The second part of the file reports the centrality metrics of all nodes in the network. This is a brief extract sorted by degree.

|Node Name | degree | clustering coefficient | betweenness| closeness | radiality | radiality reach | eccentricity	|eigenvector centrality | pagerank |
| --- | --- | --- | --- | --- | --- | --- | --- | --- | --- |
|MesoZoopl	| 26 | 0.43077 | 3.632.218 | 0.78261 | 272.222 | 272.222 | 2 | 0.25339 | 0.04346 |
|Clup | 23 | 0.4585 | 2.116.752 | 0.73469	| 263.889	| 263.889	| 2 |0.23303	| 0.03842|
|MacroBenth	| 23 | 0.41107 | 282.863 | 0.73469 | 263.889 | 263.889 | 2 | 0.21943 | 0.0389 |
|Dauph | 22 | 0.4026 | 2.418.003 | 0.72 | 261.111 | 261.111 | 2 | 	0.21513	| 0.03722|
|Chinch  | 22 | 0.50649 | 1.794.588 | 0.72 | 261.111 | 261.111 | 2 | 0.22828 | 0.03688|
|CephaCom | 22 | 0.48052 | 1.839.216 | 0.72 | 261.111 | 261.111 | 2 | 0.22571 | 0.03689|
|SelLPred | 21 | 0.5 | 193.058 | 0.70588 | 258.333 | 258.333 | 2 | 0.21318 | 0.03574|
|PelLPred | 20 | 0.45789 | 1.672.675 | 0.69231 | 255.556 | 255.556 | 2 | 0.20158 | 0.0342|

Additionally, Pyntacle will draw the graph and will save it in the *pyntacle-plots* subdirectory of the main folder of the project.
![](http://pyntacle.css-mendel.it/resources/tutorials/cs1/mauritania_local_metrics.png)


Local centrality analysis identifies *MesoZoopl*, an ensemble of mesozooplankton species such as *chaetognathes* and meroplankton, as the node with the highest *degree*, so the greatest number of connections with all other species in the Mauritania food web. This is reasonable, considering that plankton is extensively used by other species as a first nourishment. 

It can be noted, however, that several other species exhibit close degree values and, thus, that the degree alone might not be sufficient to identify keystone species in this food web. Similarly, other topological metrics like the *clustering coefficient* and *betweenness* suffer from the previous drawback, other than failing to capture any joint effect of groups of nodes. The concept of group importance can be exploited instead by means of group centrality measures, such as the key player indices.

# Key player search in food webs: *reachability* (m-reach)  <a id="kppos"></a> 
---

While local centrality measures can be good indicators of the position and immediate connectivity of nodes in networks, they provide little information on direct and indirect relationships between nodes. In fact, a node may be able to reach (i.e., be connected by one or more links with) all other nodes in a network, or this may be possible if considering all reached nodes by a group of nodes. Identifying the smallest group of nodes that achieves this goal is equivalent to finding the key player of a network.

We will hence search here for the species in the Mauritania food web that reach most of their partners by a limited number of links through a trophic network using the `kp-finder` command. In this context, the m-reach key player index fits the needs: m-reach counts the number of nodes that are reachable by a set *k* of nodes in *m* links or less. For a more detailed description of the m-reach, we refer the reader to the [What are Key-players](http://pyntacle.css-mendel.it/resources/kp_guide/kp_guide.html) and the [Quick Start Guide](http://pyntacle.css-mendel.it/resources/tutorials/startup_guide/Quick%20Start%20Guide.html) section.

The m-reach calculated on a set of size 1 (*k*=1) and a maximum distance of 1 (*m*=1) corresponds to the node degree. We can prove this by executing `kp-info` on the *MesoZoopl*  node:

`pyntacle keyplayer kp-info -t mreach -m 1 -i mauritania.adjm --nodes MesoZoopl -d ./ --no-plot`

The output will provide information on how the run performed and will produce, among other informations the following summary:

> `******************************************  RUN SUMMARY  *******************************************`
>
> `The mreach of node set:`
>
> `(MesoZoopl)`
>
> `is 26 on 37 (number of nodes reached on total number of nodes)`
>
> `This means it can reach the 72.973% of the remaining nodes in the graph in at most 1 step`
>
> `***************************************************`


and report the [results](http://pyntacle.css-mendel.it/resources/tutorials/cs1/mauritania_m-reach_kpinfo.tsv).

Although m-reach matches the node degree of *MesoZoopl* and confirms it as the most closely connected species, m-reach adds to the degree that *MesoZoopl* is able to reach alone almost all other nodes, i.e., 26 nodes out of 37, which is almost the 73% of the whole food web population. **Note**  that it may be possible that there is no single solution to this problem, and then that multiple sets of nodes exhibit the same m-reach value. For this reason, Pyntacle can be run again in search of an optimal set of size 2 that maximizes the m-reach. Using the Pyntacle's brute-force search algorithm may take longtime on big graphs, but it will be fast with this web:

`pyntacle keyplayer kp-finder -t mreach -k 2 -m 1 -I brute-force -i mauritania.adjm`

that will return the following output 

> `******************************************  RUN SUMMARY  *******************************************`
>
> `Node set size for key player search: 2`
>
> `****************************************************************************************************`
>
> `Key player sets of size 2 for positive key player index m-reach, using at most 1 steps are:`
>
> `(Dauph, MesoZoopl)`
>
> `(SelLPred, MacroBenth)`
>
> `(Clup, MesoZoopl)`
>
> `(Chinch, MesoZoopl)`
>
> `with value 32 on 37 (number of nodes reached on total number of nodes)`
>
> `The total percentage of nodes, which includes the kp-set, is 91.89%`
>
> `****************************************************************************************************`


As for the previous Pyntacle runs, this analysis will also produce a tabular report, that can be viewed at [this link](http://pyntacle.css-mendel.it/resources/tutorials/cs1/mauritania_m-reach_bruteforce.tsv) and the following plot in png format:

![mreachbf](http://pyntacle.css-mendel.it/resources/tutorials/cs1/mauritania_m-reach_bruteforce.png)

In this graph, the nodes found in all sets of size 2 are depicted in blue, and emphasis (strong line) is put on the edges that connect the immediate neighbors (adjacent vertices) of each found node.

4 sets of pairs of nodes reach the vast majority of other nodes in the network. 3 sets contain the *MesoZoopl* node, but the remaining set is made by *SelLPred* (Large selachians - predators) and *MacroBenth* (macrobenthos), two other species that have trophic interactions to the Meso zooplankton, and yet together have the same m-reach score than *MesoZoopl*, coupled with another species and never appear in combinations with it, which is quite interesting.

All the sets contain nodes that are ranked among the top 7 degree nodes, with the exception of *CephaComm* (commercial cephalopods), which is not present in any solution, despite having the same degree value (22) of *Dauph* and *Chinch* (22), which in combination with *MesoZoopl* are among the best sets.

These findings confirm that m-reach and degree, despite being semantically similar, show distinct and unique properties. 

In the context of network ecology, m-reach allowed us to figure out that the harchitecture of the network makes it widely reachable by several species, as the distances among them are short enough to allow short-range effects. In fact, any two species can reach most of the other nodes in the network, making the spreading of information of a food web, e.g., the diffusion of nutrients from a vegetable to a predator, very fast and with an immediate impact. Moreover, if we extended the m-reach distance to 2 (not shown here), we would see that the majority of species could reach all the remaining ones. In other words, the network is highly reachable when considering also indirect interactions.

We have explored here the reachability of a group of nodes and its impact on a food web. In the next section, we will explore another fundamental key player concept, the *fragmentation*.

# Evaluation of a random model <a id="rand"></a>  
---

The findings obtained in the previous paragraphs may be specific properties of the Mauritania network, or could occur by chance. To verify this, we generated and studied a [Erdos-Renyi random model](https://igraph.org/python/doc/igraph.GraphBase-class.html#Erdős_Renyi). We have created a random network with the same number of nodes and edges as the Mauritania food web to check if the key-player properties calculated for the food web could be occurred by chance.

`pyntacle generate random -n 37 -e 284`

Where `-n` is the number of vertices and `-e` is the total number of edges. This edges are assigned randomly to node pairs, but preserving Pyntacle [minimum requirements](http://pyntacle.css-mendel.it/requirements.html), so that the *in silico* network model can be reused by other Pyntacle methods. The random model can be downloaded as adjacency matrix from [here](./mauritania_random.adjm). 

The resulting network looks like:

![random](./mauritania_random.png)

**Note** that the name of the nodes is a numerical index that is assigned randomly to each node from $0$ to $N-1$,  where $N$ is the network size.

As done in the [first analysis step](#met), we will calculate the local indices of all nodes of the random network:

`pyntacle metrics local -i mauritania_random.adjm --no-plot`

Sorting nodes by degree in descending order, we will notice that the 8 highest degree nodes are lower than their rank-equivalent nodes in the Mauritania food web:

|Node Name | degree|
|:---|---|
|29 | 22|
|2 |20 |
|16 |19 |
|18 |19 |
|25 |19 |
|31 | 19 |
|33 |19 |
|17 | 18 |
|34	| 18 |

This is an excerpt of the full report produced by Pyntacle. The complete file can be downloaded [here]( mauritania_random_local.tsv).

The degree value of the top-ranked degree node, named *29*, is 22 and is lower compared to that of the *MesoZoopl* node in the Mauritania system, which is 26. This gives an idea of how single node centrality differs from a random model and how key species have a higher centrality, pinpointing their relevance in the ecological network structure. 

Let’s now turn to the original reachability problem. Using our brute-force optimization algorithm, we determined that the maximum m-reach value for a set of 2 nodes, with $m = 1$, is actually made by several combinations of node pairs, that in turn exhibit high degree values although not all the high-ranked degree nodes are part of these combinations. We can check if a random network behaves similarly by performing the same analysis on the random network, using the following command:

`pyntacle keyplayer kp-finder -I brute-force -t mreach -k 2 -m 1 -i mauritania_random.adjm --no-plot`
 
Looking at the tabular report (download it from [here](mauritania_random_mreach_bruteforce.tsv) ):

|Metric | Nodes | Value |
| --- | --- | --- |

|m-reach| 29,34 | 33 |

The best m-reach set is only one, with the percentage of nodes reached being very close to the one observed in the Mauritania food web (94,5% percent of nodes reached in the random model *vs* the 91% reached by the 4 node sets of size 2 in the Mauritania food web). This proves that the Mauritania food web presents a higher number of key nodes when compared to a random model in terms of reachability.

Again, we performed a fragmentation analysis to check if the Mauritania network is particularly resistant to fragmentation when compared to a random model.

`pyntacle keyplayer kp-finder -t F -k 2 -i --no-plot`

The [report](mauritania_random_F_greedy.tsv) shows that, even here, there is no single node that can fragment the network:

|Metric | Nodes | Value |
| :--- | --- | --- |
|F | 6,34 |0 |

Increasing the size of *k* does not increase fragmentation (data not shown).

These results show that there is not any particular difference in fragmentation between the two networks and that the high resistance to fragmentation exhibited by the food web is the same than that of the random model, so this robustness might be a product of chance, and not a specific feature of the ecosystem.

# Key-player search in food webs: *fragmentation* <a id="kpneg"></a> 
---

A set *k* of nodes that maximally disrupts a network if removed and, thus, that increases the average diameter, is known to have high *fragmentation* potential. Two fragmentation indices were implemented in Pyntacle: **F** and **dF**. We refer the user to the [Introduction to Group Centrality](http://pyntacle.css-mendel.it/resources/kp_guide/kp_guide.html) to this regard.

Then, it is interesting to compute the fragmentation of the networks under examination. To determine the vulnerable species, we will use the `pyntacle keyplayer kp-finder` command line tool. We will run a greedy-optimization search strategy that will find the optimal (not necessarily the best) set of size 2.

`pyntacle keyplayer kp-finder -k 2 -t F -i mauritania.adjm --no-plot`

will produce the following output:

> `******************************************  RUN SUMMARY  *******************************************`
>
> `Node set size for key player search: 2`
>
> `****************************************************************************************************`
>
> `Key player set of size 2 for negative key player index F is:`
>
> `(DenLInv, MesoPred)`
>
> `Final F value: 0`
>
> `Starting graph F was 0`
>
> `****************************************************************************************************`


And this [text report](http://pyntacle.css-mendel.it/resources/tutorials/cs1/mauritania_F_greedy.tsv)

The greedy optimization search returns a set of nodes (*DenLInv* and *MesoPred*) with a F value of 0. The F index varies from 0 (the graph has only one connected component) to 1 (the graph is formed by isolates). Being F a property of the graph, Pyntacle will first try to compute the starting F value of the graph and then will iteratively remove sets of nodes of size *k* until it will find an optimal set that maximizes the F. In our case, the initial F of the graph was 0, and no node set of size 2 could be found that creates at least two components, meaning that the food web topology is such that the removal of 2 species does not affect the network cohesion. A brute-force run confirmed that there is no set of size 2 that can maximize F (data not shown).

Moreover, only very large sets ($k > 8$) can create isolates and break the network, implying that the organization of the food web guarantees high stability of the network. Thus, we can speculate that the network is robust to changes in its node composition, to a certain extent.

To check if this is an organizational property of the food web and does not emerge randomly, we now compare these findings against an in silico network: the [Erdos-Renyi Model](https://en.wikipedia.org/wiki/Erd%C5%91s%E2%80%93R%C3%A9nyi_model), and check whether they are peculiar to this food web.

# Conclusions <a id="end"></a> 
---

The aim of this case study was to find the keystone species in the Mauritania network model. We first identified the species with highest degree centrality and showed that the degree alone was not sufficient to determine the keystone species. 

Through Pyntacle, we showed how degree is not directly related to reachability. The highest degree node alone, *MesoZoopl*, was not sufficient to reach the whole network (assessed with the m-reach metric), but it needed to be associated to another high degree node to reach the highest number of species by one step. 

Besides, *MesoZoopl* was not always necessary to reach the whole network, but other combinations of high degree nodes could do that. The same behavior was not observed in a random network where only one solution was found, thus remarking the fact that multiple species can contribute, together, to the overall network reachability. 

When defining fragmentation, instead, it is important to note that small node sets alone are not able to fragment both the Mauritania food web and a random network of equal size. High-degree nodes, also in this context, are not said to have any fragmentation potential and, for this particular network, robustness to fragmentation seems hence a product of chance and not dependent on the intrinsic nature of the food web. 

Of course, this conclusion cannot be generalized and it is speculative, since it should be proved more rigorously using more random networks and network models, such as the [Watts-Strogatz Small-world model](https://en.wikipedia.org/wiki/Watts%E2%80%93Strogatz_model). 

Moreover, please consider that the Mauritania food web has been symmetrized and unweighted, hence these results should not be strictly associated to the original network.

---
This concludes our case study 1. If you want to leave a feedback, please [contact us](http://pyntacle.css-mendel.it/#contacts).